In [2]:
import finnhub
import datetime, time
import pandas as pd
import pickle
import os, pathlib
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import OrdinalEncoder, OneHotEncoder, LabelEncoder
from sklearn.metrics import accuracy_score
from sklearn.utils import shuffle
import seaborn as sns
import numpy as np
from scipy import optimize
from scipy.optimize import minimize
import logging
from copy import deepcopy
import pickle
import scipy
from colog import colog
from tqdm import tqdm
import copy
import matplotlib.pyplot as plt
c_red = colog.colog(TextColor  = 'red')

import pandas_ta as ta
# for NN
import torch
import torch.nn as nn
import torch.optim as optim
from sklearn.metrics import roc_curve
from sklearn.model_selection import StratifiedKFold
from sklearn.preprocessing import LabelEncoder
from sklearn.metrics import roc_curve
device = torch.device("cuda") if (torch.cuda.is_available()) else torch.device("cpu")

logging.basicConfig(filename="logs/validing.log", 
					format='%(asctime)s %(message)s', 
					filemode='w')
# logging.shutdown()

In [3]:
# global parameter
trade_type = 'win_long' # or 'win_short'
# trade_type = 'win_short' # or 'win_long

In [4]:
def load_data_one_stock(item, condtitions = True):
 
    file = open(item, 'rb')
    load_data= pickle.load(file)
    file.close()

    # load_data['pct_1'] =  load_data['pct'].shift(1)
    # load_data['ha_colour_1'] =  load_data['ha_colour'].shift(1)
    # load_data['ha_colour_2'] =  load_data['ha_colour'].shift(2)

    # load_data['pct_diff_150_30'] = load_data['pct_sum_150'] - load_data['pct_sum_30']
    # load_data['pct_diff_30_5'] = load_data['pct_sum_30'] - load_data['pct_sum_5'] 
    # load_data['pct_diff_150_5'] = load_data['pct_sum_150'] - load_data['pct_sum_5'] 
    # load_data.dropna(inplace = True)
    
    # load_data['ha_colour_1'] = np.where(load_data['ha_colour_1'] == 'red', 0, 1)
    # load_data['ha_colour_2'] = np.where(load_data['ha_colour_2'] == 'red', 0, 1)    

    if condtitions:
        load_data =  load_data[(load_data['ha_colour_1'] == 1) & (load_data['ha_colour_2'] == 0) ]
        load_data =  load_data[(load_data['green_red_prop_10'] > 0.12) ]
        load_data =  load_data[(load_data['pct_sum_100'] > -6) ]
        
        #  safe_condition = df_stocks_dict[stock]['ha_colour'][i - 1] == 'green' and (df_stocks_dict[stock]['ha_colour'][i - 9: i - 2] == 'red').all()

        # df_stocks_dict[stock]['ha_colour'][i - 1] == 'green' and (df_stocks_dict[stock]['ha_colour'][i - 9 : i - 2] == 'red').all() \
                #    and green_red_prop_10 > 0.12 \
                #    and locals()['pct_sum_100'] > -6

    return load_data


In [5]:
def namestr(obj, namespace):
    return [name for name in namespace if namespace[name] is obj][0]

def fprint(*args):
    string = ''
    try:
        for arg in args:
            string += namestr(arg, globals()) + f' is {arg}; '
    except:
        for arg in args:
            string += namestr(arg, locals()) + f' is {arg}; '
    print(string)
     

In [6]:
def save_model(model, model_name, folder_name):
    parent_path = os.getcwd()
    folder_path = os.path.join(parent_path, folder_name)
    if not(os.path.exists(folder_path)):
        os.mkdir(folder_path)
    number = len(os.listdir(folder_path)) + 1

    if model.__class__.__name__ == 'class_models':
        file_path = os.path.join(folder_path, f'{model_name}_{number}.plk')
    else:
        if ('last' in model_name):
            file_path = os.path.join(folder_path, f'{model_name}_{number}_{model.test_profit}_{model.test_num_win}_{model.test_num_loss}_{model.valid_profit}_{model.valid_num_win}_{model.valid_num_loss}.pkl')
        else:
            file_path = os.path.join(folder_path, f'{model_name}_{number}_{model.test_profit}_{model.test_num_win}_{model.test_num_loss}_{model.valid_profit}_{model.valid_num_win}_{model.valid_num_loss}.pkl')
    
    file = open(file_path, 'wb')
    pickle.dump(model, file)
    file.close()
    print('Model save completed')

In [7]:
def rma(x, n):
    """Running moving average"""
    a = np.full_like(x, np.nan)
    a[n] = x[1:n+1].mean()
    for i in range(n+1, len(x)):
        a[i] = (a[i-1] * (n - 1) + x[i]) / n
    return a

In [8]:
def data_selection(df, dict_):
    for key, value in dict_.items():
        df = df[(df[key] >= value[0])  & (df[key] <= value[1])]
    return df

def data_selection_mix(df, dict1, dict2):


    # p = 0.88
    df1 = df
    df2 = df
    
    # df1 = df[(df['maxmin_1000'] >= 0) & (df['maxmin_1000'] < p)]
    # df2 = df[(df['maxmin_1000'] >= p) & (df['maxmin_1000'] <= 1)]

    # df1 = df[(df['rsi_5'] <= 5) & ((df['rsi_30'] < 25) | (df['rsi_30'] > 30)) ]  
    # df2 = df[(df['rsi_5'] > 5) &  (df['rsi_30'] >= 25) & (df['rsi_30'] <= 30) ] 

    for key, value in dict1.items():
        df1 = df1[(df1[key] >= value[0]) & (df1[key] <= value[1])]

    for key, value in dict2.items():
        df2 = df2[(df2[key] >= value[0]) & (df2[key] <= value[1])]
                  
    # for key, value in dict1.items():
    #     # df1 = df1[(df1[key] >= value[0]) & (df1[key] <= value[1]) & (df1['pct_sum_10'] > -1.5) & (df1['pct_sum_10'] < 1)]
    #     df1 = df1[(df1[key] >= value[0])  & (df1[key] <= value[1]) & (df1['maxmin_1000'] >= 0) & (df1['maxmin_1000'] < p)   ]

    # df2 = df
    # for key, value in dict2.items():
    #     # df2 = df2[(df2[key] >= value[0])  & (df2[key] <= value[1]) & ((df2['pct_sum_10'] >= 1) & (df2['pct_sum_10'] <= 10)  | (df2['pct_sum_10'] >= -10) & (df2['pct_sum_10'] <= -1.5))  ]
    #     df2 = df2[(df2[key] >= value[0]) & (df2[key] <= value[1]) & (df2['maxmin_1000'] >= p) & (df2['maxmin_1000'] <= 1) ]
    

    df = pd.concat([df1,df2])
    df.drop_duplicates()

    return df

In [9]:
def data_augmentation(df):

    df = df.sort_index()

    df['pct_1'] =  df['pct'].shift(1)
    df['ha_colour_1'] =  df['ha_colour'].shift(1)
    df['ha_colour_2'] =  df['ha_colour'].shift(2)
    df['ha_colour'] = np.where(df['ha_colour'] == 'red', 0, 1)
    df['ha_colour_1'] = np.where(df['ha_colour_1'] == 'red', 0, 1)
    df['ha_colour_2'] = np.where(df['ha_colour_2'] == 'red', 0, 1) 

    for window in [3, 5, 10, 20, 30, 50, 100, 150, 300]:
      df[f'pct_sum_{window}'] = df['pct'].rolling(window = window).sum()
      df[f'pct_sum_{window}'] = df[f'pct_sum_{window}'].shift(1)
      df[f'ha_pct_sum_{window}'] = df['ha_pct'].rolling(window = window).sum()
      df[f'ha_pct_sum_{window}'] = df[f'ha_pct_sum_{window}'].shift(1)

    # for window in [3, 10, 50]:
    #   df[f'pct_sum_{window}'] = df['pct'].rolling(window = window).sum()
    #   df[f'pct_sum_{window}'] = df[f'pct_sum_{window}'].shift(1)
    #   df[f'ha_pct_sum_{window}'] = df['ha_pct'].rolling(window = window).sum()
    #   df[f'ha_pct_sum_{window}'] = df[f'ha_pct_sum_{window}'].shift(1)

    for window in [3, 5, 10, 15]:
    # for window in [10, 15]:
      df[f'green_red_prop_{window}'] = df['ha_colour'].rolling(window = window).sum() / (window - df['ha_colour'].rolling(window = window).sum() + 1)    
      df[f'green_red_prop_{window}'] = df[f'green_red_prop_{window}'].shift(1)    

    df['pct_diff_150_30'] = df['pct_sum_150'] - df['pct_sum_30']
    df['pct_diff_30_5'] = df['pct_sum_30'] - df['pct_sum_5'] 
    df['pct_diff_150_5'] = df['pct_sum_150'] - df['pct_sum_5'] 
    
    
    df['max_5'] = df['open'].rolling(window = 5).max()
    df['max_10'] = df['open'].rolling(window = 10).max()
    df['max_500'] = df['open'].rolling(window = 500).max()
    df['max_100'] = df['open'].rolling(window = 100).max()
    df['max_300'] = df['open'].rolling(window = 300).max()
    df['max_1000'] = df['open'].rolling(window = 1000).max()
    df['min_5'] = df['open'].rolling(window = 5).min()
    df['min_10'] = df['open'].rolling(window = 10).min()
    df['min_500'] = df['open'].rolling(window = 500).min()
    df['min_100'] = df['open'].rolling(window = 100).min()
    df['min_300'] = df['open'].rolling(window = 300).min()
    df['min_1000'] = df['open'].rolling(window = 1000).min()
    df['maxmin_5']  = (df['open'] - df['min_5']) / (df['max_5'] - df['min_5'])
    df['maxmin_10']  = (df['open'] - df['min_10']) / (df['max_10'] - df['min_10'])
    df['maxmin_500']  = (df['open'] - df['min_500']) / (df['max_500'] - df['min_500'])
    df['maxmin_100']  = (df['open'] - df['min_100']) / (df['max_100'] - df['min_100'])
    df['maxmin_300']  = (df['open'] - df['min_300']) / (df['max_300'] - df['min_300'])
    df['maxmin_1000']  = (df['open'] - df['min_1000']) / (df['max_1000'] - df['min_1000'])

    df['maxmin_500_diff'] = df['maxmin_500'].diff()
    df['maxmin_500_avg_3'] = df['maxmin_500_diff'].rolling(window = 3).mean()
    df['maxmin_500_avg_5'] = df['maxmin_500_diff'].rolling(window = 5).mean()

    df['maxmin_1000_diff'] = df['maxmin_1000'].diff()
    df['maxmin_1000_avg_3'] = df['maxmin_1000_diff'].rolling(window = 3).mean()
    df['maxmin_1000_avg_5'] = df['maxmin_1000_diff'].rolling(window = 5).mean()


    df['change'] = df['close'].diff()
    df['gain'] = df.change.mask(df.change < 0, 0.0)
    df['loss'] = -df.change.mask(df.change > 0, -0.0)

    df['avg_gain_5'] = rma(df.gain.to_numpy(), 5)
    df['avg_loss_5'] = rma(df.loss.to_numpy(), 5)
    df['rs_5'] = df.avg_gain_5 / df.avg_loss_5
    df['rsi_5'] = 100 - (100 / (1 + df.rs_5))
    df['rsi_5'] = df['rsi_5'].shift(1)

    df['avg_gain_10'] = rma(df.gain.to_numpy(), 10)
    df['avg_loss_10'] = rma(df.loss.to_numpy(), 10)
    df['rs_10'] = df.avg_gain_10 / df.avg_loss_10
    df['rsi_10'] = 100 - (100 / (1 + df.rs_10))
    df['rsi_10'] = df['rsi_10'].shift(1)

    df['avg_gain_14'] = rma(df.gain.to_numpy(), 14)
    df['avg_loss_14'] = rma(df.loss.to_numpy(), 14)
    df['rs_14'] = df.avg_gain_14 / df.avg_loss_14
    df['rsi_14'] = 100 - (100 / (1 + df.rs_14))
    df['rsi_14'] = df['rsi_14'].shift(1)
    df['rsi_14_diff'] = df['rsi_14'].diff()
    df['rsi_14_avg_3'] = df['rsi_14_diff'].rolling(window = 3).mean()
    df['rsi_14_avg_5'] = df['rsi_14_diff'].rolling(window = 5).mean()

    df['avg_gain_20'] = rma(df.gain.to_numpy(), 20)
    df['avg_loss_20'] = rma(df.loss.to_numpy(), 20)
    df['rs_20'] = df.avg_gain_20 / df.avg_loss_20
    df['rsi_20'] = 100 - (100 / (1 + df.rs_20))
    df['rsi_20'] = df['rsi_20'].shift(1)
    df['rsi_20_diff'] = df['rsi_20'].diff()
    df['rsi_20_avg_3'] = df['rsi_20_diff'].rolling(window = 3).mean()
    df['rsi_20_avg_5'] = df['rsi_20_diff'].rolling(window = 5).mean()

    df['avg_gain_30'] = rma(df.gain.to_numpy(), 30)
    df['avg_loss_30'] = rma(df.loss.to_numpy(), 30)
    df['rs_30'] = df.avg_gain_30 / df.avg_loss_30
    df['rsi_30'] = 100 - (100 / (1 + df.rs_30))
    df['rsi_30'] = df['rsi_30'].shift(1)

    df['avg_5'] = df['pct_1'].rolling(window=5).mean()
    df['avg_10'] = df['pct_1'].rolling(window=10).mean()
    df['avg_20'] = df['pct_1'].rolling(window=20).mean()
    df['avg_30'] = df['pct_1'].rolling(window=30).mean()
    df['avg_50'] = df['pct_1'].rolling(window=50).mean()

    df['ewm_0.01'] = df['pct_1'].ewm(com=0.01, min_periods=10).mean()

    df['ewm_0.05'] = df['pct_1'].ewm(com=0.05, min_periods=10).mean()
    df['ewm_0.1'] = df['pct_1'].ewm(com=0.1, min_periods=10).mean()
    # df['pct_2'] = df['pct_1'].shift(1)
    # df['ha_pct_1'] = df['ha_pct'].shift(1)

    # df['avg_50_10'] = df['avg_50'] / (df['avg_10'] + 0.1)


    # Strategy = ta.Strategy(
    #     name="EMAs, BBs, and MACD",
    #     description="My strategy",
    #     ta=[
    #         {"kind": "stochrsi"},
    #         {"kind": "bias"},
    #         {"kind": "bop"},
    #         {"kind": "roc"},
    #         {"kind": "stochrsi"},
    #         {"kind": "inertia"},
    #         {"kind": "ao"},
    #         {"kind": "apo"},
    #     ]
    # )

    # df.ta.strategy(Strategy)

    # shiftcolumns = ['STOCHRSIk_14_14_3_3',
    #    'STOCHRSId_14_14_3_3', 'BIAS_SMA_26', 'BOP',
    #    'ROC_10', 'INERTIA_20_14', 'AO_5_34',
    #    'APO_12_26']
    # for column in shiftcolumns:
    #     df[column] = df[column].shift(1)

    # columns = list(set(df.columns) - set(['close', 'gain', 'ha_c', 'open', 'high', 'low', 'win_long', 'win_short', 'result', 'change', 'ha_o','loss', 'pct', 'ha_colour']))
    dropcolumns = ['close', 'gain', 'ha_c', 'open', 'high', 'low',  'change', 'ha_o','loss', 'pct', 'ha_colour',  \
                    'avg_gain_5',  'avg_gain_10',  'avg_gain_14', 'avg_gain_30', 'avg_gain_20',
                     'rs_5', 'rs_10', 'rs_14', 'rs_20', 'rs_30', 'avg_loss_5', 'avg_loss_10', 'avg_loss_14','avg_loss_20', 'avg_loss_30',  'pct_sum_1', 'ha_pct_sum_1', 'ha_pct', 
                     'max_5', 'max_10', 'max_100', 'max_300', 'max_500', 'max_1000',  'min_5', 'min_10', 'min_100', 'min_300', 'min_500', 'min_1000']
    
    # dropcolumns += ['green_red_prop_10', 'green_red_prop_15',
    #    'green_red_prop_5', 'ha_pct_sum_10', 'ha_pct_sum_100', 'ha_pct_sum_150',
    #    'ha_pct_sum_20', 'ha_pct_sum_3', 'ha_pct_sum_30', 'ha_pct_sum_300',
    #    'ha_pct_sum_5', 'ha_pct_sum_50', 'pct_sum_10', 'pct_sum_100',
    #    'pct_sum_150', 'pct_sum_20', 'pct_sum_3', 'pct_sum_30', 'pct_sum_300',
    #    'pct_sum_5', 'pct_sum_50']
    
    

    for column in dropcolumns:
        try:
            df.drop(columns = [column], inplace = True)
        except:
            pass
    
    df.dropna(inplace=True)
    df = df.reindex(sorted(df.columns), axis=1)

    return df

In [30]:
conditions = False
folder_save_models_name = f'models_v36_{trade_type}_numpartslist_cond{conditions}'
parent_path = os.getcwd()
# folder_path = os.path.join(parent_path, 'historical_data/onestock/5m_aug')
folder_path = os.path.join(parent_path, 'historical_data/onestock/5m_raw_aug')

data_train_whole = pd.DataFrame()
data_test_whole = pd.DataFrame()
data_whole = pd.DataFrame()


Group1_0 =['APH',   'TEL',  'BRK.B',  'BLK',  'MMC',  'HON',  'ECL',  'MSFT',  'AAPL',  'CTAS',  'JCI',  'ITW',  'ADP',  'ACN',  'EMR',  'MSI',  'DIS', 
             'ISRG',  'ROP',  'ETN',  'AXP',  'LIN',  'ADI',  'AVGO',  'INTU',  'MCO',  'TXN',  'PH',  'SBUX',  'CSCO',  'AJG',  'NXPI',  'HD',  'JPM',  'CDNS', 
             'ROK',  'QCOM',  'MCHP',  'SPG',  'CARR',  'COST',  'SYK',  'IQV',  'TT',  'GS',  'MSCI',  'TDG',  'GOOGL',  'V',  'ADSK']

Group0_75 = ['ADSK', 'AMAT', 'KLAC', 'ADBE', 'GOOG', 'BAC', 'COF', 'SPGI', 'SHW', 'ON', 'AMZN', 'ABT', 'SNPS', 'AON', 'LRCX', 'ICE', 'META', 'MS', 
             'NKE', 'IDXX', 'APD', 'NVDA', 'CSX', 'AIG', 'LOW', 'EL', 'MDT', 'PNC', 'GM', 'MMM', 'NOW', 'CRM', 'FTNT', 'TJX', 'DHR', 'MA', 'F', 
             'INTC', 'PLD', 'CAT', 'TGT', 'DHI', 'FCX', 'CB', 'PEP', 'MNST', 'C',  'NSC',  'GD',  'CMG']

num_items= len(os.listdir(folder_path))
for i in range(num_items):
    item = os.listdir(folder_path)[i]

    stock_name = item[str.find(item, 'df_') + 3 : str.find(item, '_20')]

    if stock_name in ['AAPL']: #Group1_0:

        data_path = os.path.join(folder_path, item)
        data = load_data_one_stock(data_path, condtitions = conditions)
        data = data_augmentation(data)
        # data = data[['pct_1', 'ewm_0.1', 'win_long', 'win_short']]
        data_whole = pd.concat([data_whole, data])
        # data_train, data_test = train_test_split(data, train_size = 0.125, shuffle = False)
        # data, _ = train_test_split(data, train_size = 0.5, shuffle = False)
        data_train, data_test = train_test_split(data, train_size = 0.7, shuffle = False)

        n = data.shape[0]    
        data_train_whole = pd.concat([data_train_whole, data_train])
        data_test_whole = pd.concat([data_test_whole, data_test])

# data_train_whole, data_valid_whole = train_test_split(data_train_whole, train_size = 0.7, shuffle = False)

data_train_whole_copy = data_train_whole
# data_valid_whole_copy = data_valid_whole
data_test_whole_copy = data_test_whole

In [11]:
folder_path = os.path.join(parent_path, 'historical_data/onestock/5m_raw_test_start_20230716_aug')

data_test_whole_2 = pd.DataFrame()


Group1_0 =['APH',   'TEL',  'BRK.B',  'BLK',  'MMC',  'HON',  'ECL',  'MSFT',  'AAPL',  'CTAS',  'JCI',  'ITW',  'ADP',  'ACN',  'EMR',  'MSI',  'DIS', 
             'ISRG',  'ROP',  'ETN',  'AXP',  'LIN',  'ADI',  'AVGO',  'INTU',  'MCO',  'TXN',  'PH',  'SBUX',  'CSCO',  'AJG',  'NXPI',  'HD',  'JPM',  'CDNS', 
             'ROK',  'QCOM',  'MCHP',  'SPG',  'CARR',  'COST',  'SYK',  'IQV',  'TT',  'GS',  'MSCI',  'TDG',  'GOOGL',  'V',  'ADSK']


Group0_75 = ['ADSK', 'AMAT', 'KLAC', 'ADBE', 'GOOG', 'BAC', 'COF', 'SPGI', 'SHW', 'ON', 'AMZN', 'ABT', 'SNPS', 'AON', 'LRCX', 'ICE', 'META', 'MS', 
             'NKE', 'IDXX', 'APD', 'NVDA', 'CSX', 'AIG', 'LOW', 'EL', 'MDT', 'PNC', 'GM', 'MMM', 'NOW', 'CRM', 'FTNT', 'TJX', 'DHR', 'MA', 'F', 
             'INTC', 'PLD', 'CAT', 'TGT', 'DHI', 'FCX', 'CB', 'PEP', 'MNST', 'C',  'NSC',  'GD',  'CMG']

num_items= len(os.listdir(folder_path))
for i in range(num_items):
    item = os.listdir(folder_path)[i]

    stock_name = item[str.find(item, 'df_') + 3 : str.find(item, '_20')]

    if stock_name in Group1_0:

        data_path = os.path.join(folder_path, item)
        data = load_data_one_stock(data_path, condtitions = conditions)
        data = data_augmentation(data)
        # data = data[['pct_1', 'ewm_0.1', 'win_long', 'win_short']]
        data_test_whole_2 = pd.concat([data_test_whole_2, data])

data_test_whole_2_copy = data_test_whole_2

In [12]:
if False:
    conditions = False
    parent_path = os.getcwd()
    # folder_path = os.path.join(parent_path, 'historical_data/onestock/5m_aug')
    folder_path = os.path.join(parent_path, 'historical_data/onestock/5m_raw_test_aug')

    data_test_raw = pd.DataFrame()

    num_items= len(os.listdir(folder_path))
    for i in range(num_items):
        item = os.listdir(folder_path)[i]

        data_path = os.path.join(folder_path, item)
        data = load_data_one_stock(data_path, condtitions = conditions)
        data = data_augmentation(data)

        data_test_raw = pd.concat([data_test_raw , data])
    
    data_test_raw_copy =  data_test_raw
    
    data_test_raw_copy['win_long'].sum(), data_test_raw_copy['win_short'].sum()

In [32]:
data_whole.columns, data_whole.shape, data_train_whole.shape, data_test_whole.shape
# data_whole.columns, data_whole.shape, data_train_whole.shape, data_valid_whole.shape

(Index(['avg_10', 'avg_20', 'avg_30', 'avg_5', 'avg_50', 'ewm_0.01', 'ewm_0.05',
        'ewm_0.1', 'green_red_prop_10', 'green_red_prop_15', 'green_red_prop_3',
        'green_red_prop_5', 'ha_colour_1', 'ha_colour_2', 'ha_pct_sum_10',
        'ha_pct_sum_100', 'ha_pct_sum_150', 'ha_pct_sum_20', 'ha_pct_sum_3',
        'ha_pct_sum_30', 'ha_pct_sum_300', 'ha_pct_sum_5', 'ha_pct_sum_50',
        'maxmin_10', 'maxmin_100', 'maxmin_1000', 'maxmin_1000_avg_3',
        'maxmin_1000_avg_5', 'maxmin_1000_diff', 'maxmin_300', 'maxmin_5',
        'maxmin_500', 'maxmin_500_avg_3', 'maxmin_500_avg_5', 'maxmin_500_diff',
        'pct_1', 'pct_diff_150_30', 'pct_diff_150_5', 'pct_diff_30_5',
        'pct_sum_10', 'pct_sum_100', 'pct_sum_150', 'pct_sum_20', 'pct_sum_3',
        'pct_sum_30', 'pct_sum_300', 'pct_sum_5', 'pct_sum_50', 'rsi_10',
        'rsi_14', 'rsi_14_avg_3', 'rsi_14_avg_5', 'rsi_14_diff', 'rsi_20',
        'rsi_20_avg_3', 'rsi_20_avg_5', 'rsi_20_diff', 'rsi_30', 'rsi_5',
        'w

In [14]:
def np_arange_cust(
        *args, rtol: float=1e-05, atol: float=1e-08, include_start: bool=True, include_stop: bool = False, **kwargs
):
    """
    Combines numpy.arange and numpy.isclose to mimic open, half-open and closed intervals.

    Avoids also floating point rounding errors as with
    >>> np.arange(1, 1.3, 0.1)
    array([1., 1.1, 1.2, 1.3])

    Parameters
    ----------
    *args : float
        passed to np.arange
    rtol : float
        if last element of array is within this relative tolerance to stop and include[0]==False, it is skipped
    atol : float
        if last element of array is within this relative tolerance to stop and include[1]==False, it is skipped
    include_start: bool
        if first element is included in the returned array
    include_stop: bool
        if last elements are included in the returned array if stop equals last element
    kwargs :
        passed to np.arange

    Returns
    -------
    np.ndarray :
        as np.arange but eventually with first and last element stripped/added
    """
    # process arguments
    if len(args) == 1:
        start = 0
        stop = args[0]
        step = 1
    elif len(args) == 2:
        start, stop = args
        step = 1
    else:
        assert len(args) == 3
        start, stop, step = tuple(args)

    arr = np.arange(start, stop, step, **kwargs)
    if not include_start:
        arr = np.delete(arr, 0)

    if include_stop:
        if np.isclose(arr[-1] + step, stop, rtol=rtol, atol=atol):
            arr = np.c_[arr, arr[-1] + step]
    else:
        if np.isclose(arr[-1], stop, rtol=rtol, atol=atol):
            arr = np.delete(arr, -1)
    return arr

def np_arange_closed(*args, **kwargs):
    return np_arange_cust(*args, **kwargs, include_start=True, include_stop=True)

def np_arange_open(*args, **kwargs):
    return np_arange_cust(*args, **kwargs, include_start=True, include_stop=False)

In [15]:
def arange(start, stop, step=1, endpoint=True):
    arr = np.arange(start, stop, step)
    if len(arr) > 0:
        if endpoint and arr[-1] != stop:
            arr = np.concatenate([arr,[stop]])
    

    return arr

In [16]:
# def wins_summary(data, trade_type = 'win_long'):
def wins_summary(data, trade_type, part_num, show = False):
        data = data.dropna()
        if trade_type == 'win_long':
                num_wins = (data['win_long'] == 1).sum()
                num_loses = (data['win_long'] == 0).sum()
        else:
                num_wins = (data['win_long'] == 0).sum()
                num_loses = (data['win_long'] == 1).sum()


        if num_loses== 0:
                prop = num_wins
        else:
                prop = num_wins / num_loses

        fun = 200 * num_wins - 600 * num_loses

        maxmin5 = data['maxmin_5'].mean()
        maxmin10 = data['maxmin_10'].mean()
        maxmin300 = data['maxmin_300'].mean()
        maxmin500 = data['maxmin_500'].mean()
        maxmin1000 = data['maxmin_1000'].mean()
        maxmin1000_avg5 = data['maxmin_1000_avg_5'].mean()
        ewm0_01_max  = data['ewm_0.01'].max()

        # print(f'''Part {i} num_wins {num_wins}, num_loses {num_loses} proportion is {prop :.2f}, fun {fun}, maxmein5 {maxmin5:.2f}, maxmin10 {maxmin10:.2f}, maxmin300 {maxmin300:.2f},maxmin500 {maxmin500:.2f}, maxmin1000 {maxmin1000:.2f}, maxmin1000_avg5 {maxmin1000_avg5}''')
        if show == True:
                print(f'''Part {part_num} num_wins {num_wins}, num_loses {num_loses} proportion is {prop :.2f}, fun {fun} ''')
        
        return num_wins, num_loses, fun

In [16]:
# total = 100000
# wins = np.arange(0, 100, 10)
# loses = np.arange(1, 100, 9)
# x, y = np.meshgrid(wins, loses)
# z = x * np.log(x - y)/y
# ax = plt.figure().add_subplot(projection='3d')
# ax.plot_surface(x, y, z)
# ax.set_zlim(-10.01, 10.01)
# plt.plot(wins, wins/loses)

In [17]:
def fun(dict_, data, n_parts , trade_type, data_type, display = True):
        global g_k
        n = data.shape[0]
        total_wins = 0
        total_loses = 0
        fun_values = []
        for i in range(n_parts):
                data_ = data[int((i * n) / (n_parts)): int((i + 1) * n / (n_parts)) ]

                data_  = data_selection(data_, dict_)

                num_wins, num_loses, fun = wins_summary(data_, trade_type, i)

                # if fun < 0: 
                #         profit = 0
                # else:
                #         profit = fun / 1000
                profit = fun / 1000

                total_wins += num_wins
                total_loses += num_loses

                if num_loses == 0:
                        prop = num_wins
                else:
                        prop = num_wins / num_loses

                if num_wins >= num_loses:
                        if num_loses == 0:
                                prop = num_wins
                        else:
                                prop = num_wins / num_loses
                else:   
                        prop = num_wins / num_loses
                        if num_wins == 0:
                                prop = - num_loses
                        else:
                                prop = - num_loses / num_wins
                
                # if num_loses == 0:
                #         prop = num_wins
                # else:
                #         prop = num_wins / num_loses
                
                logarg = abs(num_wins - num_loses) / 2
                if num_wins - num_loses == 0:
                        lgp = 0
                elif num_wins > num_loses:
                        lgp = np.emath.logn(3000, logarg)
                else:
                        lgp = - np.emath.logn(3000, logarg)

                # fv = prop  + lgp / 10 + profit
                # fv  = prop / (np.emath.logn(2, abs(num_wins - num_loses)) + 1) +  lgp  + profit
                # fv = profit + lgp / 10 
                # fv = prop
                # fv = num_wins * 200 - num_loses * 230
                if data_type == 'valid': 
                        fv = num_wins * 200 - num_loses * 600
                else: 
                        fv = num_wins * 200 - num_loses * g_k
                
                # fv = total_wins * 200 - total_loses * 600
                fun_values.append(fv)
        
        if total_loses == 0:
                prop = total_wins
        else:
                prop = total_wins / total_loses
        
        if total_wins - total_loses <= 0:
                logarg = 1
        else:
                logarg = (total_wins - total_loses) / 2

        # functional = prop  + np.emath.logn(3000, logarg)
        # functional = fun
        if fun < 0: 
                profit = 0
        else:
                profit = fun / 1000
        functional_ = prop  + np.emath.logn(3000, logarg) + profit

        # functional = np.mean(fun_values) - np.std(fun_values) / 2
        mean = np.mean(fun_values)
        std =  max(1, np.std(fun_values))
        # functional =  mean +  3 * mean / std
        functional = mean
        # functional = (mean + 1) / std
        # functional = total_wins * 200 - total_loses * 300 stAGE1 
        # functional = total_wins * 200 - total_loses * 600

        if total_loses > 1000: k = 1.2
        elif total_loses > 500: k = 1.2
        elif total_loses > 300: k = 1.2
        elif total_loses > 50: k = 2
        else: k = 3

        x1,x2 = 100, 1000
        y1,y2 = 600, 230
        k = (total_wins - x1) / (x2 - x1) * (y2-y1) + y1
        if k > 600 : k = 600

        # if total_loses > 1000: k = 240
        # elif total_loses > 500: k = 400
        # elif total_loses > 200: k = 600
        # elif total_loses > 50: k = 600
        # else: k = 600
        k = (total_wins * 200 - 700) / (total_loses + 1)
        if k > 600 : k = 600
        if k < 250 : k = 250

        # functional = mean +  mean / std +  (total_wins - total_loses * k)
        # functional = mean +  mean / std
        
        if display == True:
                print(f'{data_type}:: Functional value is {functional:.3f}, mean is {mean:.3f}, std is {std:.3f}, profit is {profit:.3f}, prop is {prop:.3f}, total_wins is {total_wins}, total_loses is {total_loses}')

        return functional, k
    

In [19]:
class stages():
    '''
    type1: [0, 1]; type2: [0, 100]; type 3: [-10, 10]
    '''
    def __init__(self, stage_num, param_num):
        if stage_num == 0:
            self.step = {'type1': 0.1, 'type2': 5, 'type3': 1}
            self.enumeration_type = 'sequential'
            self.num_cycles_without_fun_change_SP = param_num * 1   # was 3
        if stage_num == 1:
            self.step = {'type1': 0.05, 'type2': 2, 'type3': 0.3}
            self.enumeration_type = 'sequential'
            self.num_cycles_without_fun_change_SP =  5 #param_num * 1   # was 2
        if stage_num == 2:
            self.step = {'type1': 0.01, 'type2': 1, 'type3': 0.1}
            self.enumeration_type = 'sequential'
            self.num_cycles_without_fun_change_SP =  3 #param_num * 1   # was 2


def fun_p_opt(j, stage, data_train, data_valid, param_list, max_fun_value, max_valid_fun_value, 
              p0_limit, p1_limit, p0, p1, p, param_type, trade_type, n_parts, p_opt, fun_was_improved, flag_equal):
    global g_k
    global p0_opt_valid, p1_opt_valid, opt_valid_fun_value, opt_fun_value
          
    dict_ = {}
    for i, key in enumerate(param_list):
        dict_[key] = [p0[i], p1[i]]
        
    # calc_train_value = fun(dict_, data_train, n_parts, trade_type, 'train')
    # calc_valid_value = fun(dict_, data_valid, n_parts, trade_type, 'valid')
    # fun_value = calc_train_value + calc_valid_value
    
 
    fun_value, k = fun(dict_, data_train, 1, trade_type, 'train', display=False)
    valid_fun_value, _= fun(dict_, data_valid, 1, trade_type, 'valid', display=False)
    fun(dict_, data_test_whole, 1, trade_type, 'test', display=False)

    # fun_value = E(x) - 1(2)*std
    # if calc_valid_value >= max_valid_fun_value:
    #     if fun_value == max_fun_value and flag_equal:
    #         p_opt = p
    #         flag_equal = False
    #     if fun_value  > max_fun_value:
    #         max_fun_value = fun_value
    #         max_valid_fun_value = calc_valid_value
    #         p_opt = p
    #         fun_was_improved = True
    
    if fun_value == max_fun_value and flag_equal:
        p_opt = p
        flag_equal = False
    # if (fun_value  > max_fun_value and valid_fun_value >= max_valid_fun_value):
    if valid_fun_value >= max_valid_fun_value and fun_value>=max_fun_value:
        max_valid_fun_value = valid_fun_value

        p0_opt_valid = p0
        p1_opt_valid = p1
        opt_valid_fun_value = valid_fun_value
        opt_fun_value = fun_value

    if (fun_value  > max_fun_value):
    # if (fun_value  > max_fun_value and valid_fun_value >= max_valid_fun_value):

        p_opt = p
        fun_was_improved = True
        max_fun_value = fun_value
        max_valid_fun_value = valid_fun_value
        # if max_valid_fun_value > max_fun_value: max_valid_fun_value = max_fun_value
        
        # g_k = k
        # max_fun_value, k = fun(dict_, data_train, 50, trade_type, 'train')
        # max_valid_fun_value, _ = fun(dict_, data_valid, 50, trade_type, 'valid')
        # print(f"GLOBAL k is {g_k}, k is {k}")

    return p_opt, fun_was_improved, flag_equal, max_fun_value, max_valid_fun_value 
    

def stage_cycle(stage, data_train, param_list, max_fun_value, max_valid_fun_value, p0_limit, p1_limit, p0, p1, param_type, param_num, trade_type, n_parts):
    global g_k
    global p0_opt_valid, p1_opt_valid, opt_valid_fun_value, opt_fun_value
    cond = True
    num_cycles_without_fun_changes = 0
    j = 0
    #---K-fold optimization---
    data_train_whole = data_train
    #  -------
    
    data_train, data_valid = train_test_split(data_train_whole, train_size = 0.8, shuffle = False)

    while cond: 
        print(f'Cycle number is {j}')

        dict_ = {}
        for i, key in enumerate(param_list):
            dict_[key] = [p0[i], p1[i]]

        
        #---K-fold optimization---
        #     data_train = 
            # data_train, data_valid = train_test_split(data_train_whole, train_size = 0.2, shuffle = True)
        # #

        max_fun_value , g_k = fun(dict_, data_train, 1, trade_type, 'train')
        max_valid_fun_value , _ = fun(dict_, data_valid, 1, trade_type, 'valid')
        fun(dict_, data_test_whole, 1, trade_type, 'test')

        p0_opt_valid = p0
        p1_opt_valid = p1
        opt_fun_value = max_fun_value
        opt_valid_fun_value = max_valid_fun_value

        # if max_valid_fun_value > max_fun_value: max_valid_fun_value = max_fun_value

        print(f"GLOBAL k is {g_k}")

        j = np.random.randint(param_num)
        fun_was_improved = False

        if np.random.random() < 0.5: # optimization starts from p0
            
            p1_opt = p1[j]
            p1[j] = p1_limit[j]  # reset the p1
            p_opt = p0[j]
            flag_equal = True
            for p in arange(p0_limit[j], p1[j], stage.step[param_type[j]]):
                p0[j] = p
                p_opt, fun_was_improved, flag_equal, max_fun_value, max_valid_fun_value  = fun_p_opt(j, stage, data_train, data_valid, param_list, max_fun_value, max_valid_fun_value,
                                                 p0_limit, p1_limit, p0, p1, p, param_type, trade_type, n_parts, p_opt, fun_was_improved, flag_equal)
                 
            p0[j] = p_opt
            if fun_was_improved == False: p1[j] = p1_opt
            # if p_opt != p0[j]: p0[j] = p_opt

            # finding p1 optimal value
            p_opt = p1[j]   
            flag_equal = True
            for p in arange(p1_limit[j], p0[j], -stage.step[param_type[j]]):
                p1[j] = p

                p_opt, fun_was_improved, flag_equal, max_fun_value, max_valid_fun_value  = fun_p_opt(j, stage, data_train, data_valid, param_list, max_fun_value, max_valid_fun_value,
                                                 p0_limit, p1_limit, p0, p1, p, param_type, trade_type, n_parts, p_opt, fun_was_improved, flag_equal)
            # if p_opt != p1[j]: p1[j] = p_opt
            p1[j] = p_opt
        
        else: # optimization starts from p1

            p0_opt = p0[j]
            p0[j] = p0_limit[j] # reset the p0
            p_opt = p1[j]
            flag_equal = True
            for p in arange(p1_limit[j], p0[j], -stage.step[param_type[j]]):
                p1[j] = p

                p_opt, fun_was_improved, flag_equal, max_fun_value, max_valid_fun_value  = fun_p_opt(j, stage, data_train, data_valid, param_list, max_fun_value, max_valid_fun_value,
                                                 p0_limit, p1_limit, p0, p1, p, param_type, trade_type, n_parts, p_opt, fun_was_improved, flag_equal)
            # if p_opt != p1[j]: p1[j] = p_opt
            p1[j] = p_opt
            if fun_was_improved == False: p0[j] = p0_opt

            # finding p0 optimal value
            p_opt = p0[j] 
            flag_equal = True
            for p in arange(p0_limit[j], p1[j], stage.step[param_type[j]]):
                p0[j] = p
                
                p_opt, fun_was_improved, flag_equal, max_fun_value, max_valid_fun_value  = fun_p_opt(j, stage, data_train, data_valid, param_list, max_fun_value, max_valid_fun_value,
                                                 p0_limit, p1_limit, p0, p1, p, param_type, trade_type, n_parts, p_opt, fun_was_improved, flag_equal)
            # if p_opt != p0[j]: p0[j] = p_opt
            p0[j] = p_opt
            
        j += 1
        if j >= param_num: j = 0
        if fun_was_improved == False:
            num_cycles_without_fun_changes += 1
        else: 
            num_cycles_without_fun_changes = 0
       
        print(f'p0 is {p0}')
        print(f'p1 is {p1}')
        print(f'p0_opt_valid is {p0_opt_valid}')
        print(f'p1_opt_valid is {p1_opt_valid}')
        
        print(f'num_cycles_without_fun_changes is {num_cycles_without_fun_changes}, max_fan_value is {max_fun_value}, max_valid_fan_value is {max_valid_fun_value}')
            
        cond = num_cycles_without_fun_changes < stage.num_cycles_without_fun_change_SP

    return p0_opt_valid, p1_opt_valid, max_fun_value

def parameters_optimization(param_list, fun, data_train, n_parts, trade_type):
    global g_k
    stage = 0
    param_num = len(param_list)

    stage0 = stages(0, param_num)
    stage1 = stages(1, param_num)
    stage2 = stages(2, param_num)
 
    # Parameters initialization
    p0 = np.zeros(param_num)
    p1 = np.zeros(param_num)
    p0_limit = np.zeros(param_num)
    p1_limit = np.zeros(param_num)
    param_type = []

    for i, key in enumerate(param_list):
        p0_limit[i] = param_list[key][0]
        p1_limit[i] = param_list[key][1]
        p0[i] = param_list[key][0]
        p1[i] = param_list[key][1]

        if p0[i] == 0 and p1[i] == 1:
            param_type.append('type1')
        if p0[i] == -1 and p1[i] == 1:
            param_type.append('type1')
        if p0[i] == 0 and p1[i] == 100:
            param_type.append('type2')
        if p0[i] == -10 and p1[i] == 10:
            param_type.append('type3')
    
    dict_ = {}
    for key in param_list:
        dict_[key] = [param_list[key][0], param_list[key][1]]

    # max_fun_value = fun(dict_, data_train, n_parts, trade_type, 'train')
    # max_valid_fun_value = fun(dict_, data_valid, n_parts, trade_type, 'valid')
    max_valid_fun_value = -10**8
    max_fun_value = -10**8
    # g_k = 230

    # p0 = [0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, -1.0, -0.14999999999999925, -0.13999999999999924, -3.0, -2.0, -10.0, 36.0, 30.0, 0.0, 30.0, -2.1999999999999815, -0.9999999999999787]
    # p1 = [0.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 0.10999999999999921, 1.0, 10.0, 10.0, 10.0, 45.0, 100.0, 45.0, 100.0, 1.2999999999999794, 1.0]

    # p0 = [0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, -1.0, -1.0, -0.13999999999999924, -3.0, -10.0, -10.0, 36.0, 30.0, 0.0, 30.0, -10.0, -10.0]
    # p1 = [0.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 0.049999999999999156, 0.10999999999999921, 1.0, 10.0, 0.0, 0.0, 100.0, 35.0, 40.0, 100.0, 1.2999999999999794, 10.0]
    # p0 = [  0,    0,    0,    0.4,   0,    0,    0,   -1,   -1,   -1,  -10,  -10,
    #     -10,   40,   60,    0,    0,    0,  -10,  -10,   -2,   -2,  -10,  -10, -10 ]

    # p1 = [  0.1,   0.1,   1,    1,    1,    1,    1,    0.4,   1,    0.3,  10,   10,
    #     10,   55,  100,  100,  100,   10,    3.3,  10,    9,    2.2,  10,    8,  10 ]
    
    p0 = [0.0, 0.0, 0.0, 0.4, 0.0, 0.0, 0.0, -0.40000000000000013, -0.15999999999999925, -1.0, -10.0, -1.5000000000000302, -10.0, 45.0, 55.0, 0.0, 0.0, -10.0, -10.0, -10.0, -2.0, -1.8999999999999808, -10.0, -10.0, -10.0]
    p1 = [0.18999999999999928, 0.1000000000000002, 0.2999999999999994, 1.0, 1.0, 1.0, 1.0, 0.20000000000000018, 0.0999999999999992, 1.0, 1.0, 10.0, 10.0, 56.0, 100.0, 60.0, 100.0, 3.300000000000024, 10.0, 5.0, 10.0, 10.0, 10.0, 9.0, 10.0]

    # max_fun_value = fun(dict_, data_train, 50, trade_type, 'train')

    # Stage 0: grid parameters with big step. Linear order of selection (or random order selectino) p*1 or p*2 starts with 50% random change
    # Stage 1: grid parameters with middle step. Linear order of selection. p*1 or p*2 starts with 50% random change
    # Stage 2: grid parameters with low step. Linear order of selection. p*1 or p*2 starts with 50% random change
    
    print(f'Stage number is 0')
    p0, p1, max_fun_value = stage_cycle(stage0, data_train, param_list, max_fun_value, max_valid_fun_value,  p0_limit, p1_limit, p0, p1, param_type, param_num, trade_type, n_parts)
    print(f'Stage number is 1')
    p0, p1, max_fun_value = stage_cycle(stage1, data_train, param_list, max_fun_value, max_valid_fun_value,  p0_limit, p1_limit, p0, p1, param_type, param_num, trade_type, n_parts)
    print(f'Stage number is 2')
    p0, p1, max_fun_value = stage_cycle(stage2, data_train, param_list, max_fun_value, max_valid_fun_value,  p0_limit, p1_limit, p0, p1, param_type, param_num, trade_type, n_parts)
    
    return p0, p1, max_fun_value


In [18]:
class class_models():
  def __init__(self, p0, p1) :
    self.p0 = p0
    self.p1 = p1  

    self.dict_ = {}
    for i, key in enumerate(dict_.keys()):
      self.dict_[key] = [p0[i], p1[i]]

In [45]:
#resaving models with proper names
data_train_whole = data_train_whole_copy
# data_valid_whole = data_valid_whole_copy
data_test_whole =  data_test_whole_copy
version = '104'

folder_path = 'models_v102'

folder_save_models_name = f'models_v102_resaved'
parent_path = os.getcwd()
folder_path = os.path.join(parent_path, folder_path)

for i, name in enumerate(os.listdir(folder_path)):
    data_path = os.path.join(folder_path, name)
    file = open(data_path, 'rb')
    model = pickle.load(file)

    for i, key in enumerate(dict_):
        dict_[key] = [model.p0[i], model.p1[i]]

    fun_value, k = fun(dict_, data_train_whole, 1, trade_type, 'train')
    
    model_name = f'model_v{str(version)}_fv{fun_value:.0f}'
    folder_name = f'models_v{str(version)}'
    save_model(model, model_name, folder_name)

train:: Functional value is 14400.000, mean is 14400.000, std is 1.000, profit is 14.400, prop is 8.538, total_wins is 111, total_loses is 13
Model save completed
train:: Functional value is 4000.000, mean is 4000.000, std is 1.000, profit is 4.000, prop is 4.000, total_wins is 80, total_loses is 20
Model save completed
train:: Functional value is 7600.000, mean is 7600.000, std is 1.000, profit is 7.600, prop is 7.750, total_wins is 62, total_loses is 8
Model save completed
train:: Functional value is 9400.000, mean is 9400.000, std is 1.000, profit is 9.400, prop is 6.917, total_wins is 83, total_loses is 12
Model save completed
train:: Functional value is 17600.000, mean is 17600.000, std is 1.000, profit is 17.600, prop is 5.588, total_wins is 190, total_loses is 34
Model save completed
train:: Functional value is 6200.000, mean is 6200.000, std is 1.000, profit is 6.200, prop is 5.214, total_wins is 73, total_loses is 14
Model save completed
train:: Functional value is 10000.000, 

In [44]:
data_train_whole.index.min(), data_train_whole.index.max()

(Timestamp('2022-08-02 15:10:00-0400', tz='America/New_York'),
 Timestamp('2022-09-09 15:50:00-0400', tz='America/New_York'))

In [43]:
# plt.plot(data_test_whole.index)
data_test_whole.index.min(), data_test_whole.index.max()

(Timestamp('2022-08-30 10:50:00-0400', tz='America/New_York'),
 Timestamp('2022-09-23 09:45:00-0400', tz='America/New_York'))

In [33]:
if True:
  data_train_whole = data_train_whole_copy
  # data_valid_whole = data_valid_whole_copy
  data_test_whole =  data_test_whole_copy
else:
  data_train_whole, data_test_whole = train_test_split(data_test_whole_2, train_size=0.66, shuffle=False)

global opt_fun_value, opt_valid_fun_value

# dict_= {
#         'maxmin_1000' : [0, 1],
#         'maxmin_500'  : [0, 1],  
#         'maxmin_300'  : [0, 1],  
#         'maxmin_5'  : [0, 1],   
#         'ha_colour_1': [0, 1],
#         'ewm_0.05': [0, 1],
#         'ewm_0.01': [0, 1],
#         'pct_sum_150': [-10, 10],
#         'pct_sum_30' : [-10, 10],
#         'rsi_20': [0, 100],
#         'rsi_5' : [0, 100],
#         'rsi_14_avg_5' : [-10, 10],
#         'rsi_20_avg_3' : [-10, 10]
#         }
# dict_= {
#         'maxmin_1000' : [0, 1],
#         # 'maxmin_500'  : [0, 1],  
#         # 'maxmin_300'  : [0, 1], 
#         'maxmin_10' : [0, 1], 
#         'maxmin_5'  : [0, 1],   
#         'ha_colour_1': [0, 1],
#         'ha_colour_2': [0, 1],
#         'ewm_0.05': [0, 1],
#         'ewm_0.01': [0, 1],
#         'ewm_0.1': [0, 1],
#         # 'pct_sum_150': [-10, 10],
#         # 'pct_sum_30' : [-10, 10],
#         'pct_sum_10' : [-10, 10],
#         'rsi_30': [0, 100],
#         'rsi_10' : [0, 100],
#         # 'rsi_20': [0, 100],
#         # 'rsi_5' : [0, 100],
#         'rsi_14_avg_5' : [-10, 10],
#         'rsi_20_avg_3' : [-10, 10]
#         }
class class_models():
  def __init__(self, p0, p1) :
    self.p0 = p0
    self.p1 = p1  

    self.dict_ = {}
    for i, key in enumerate(dict_.keys()):
      self.dict_[key] = [p0[i], p1[i]]

# first variant with models_v103
dict_= {
        'maxmin_1000' : [0, 1],
        'maxmin_500'  : [0, 1],  
        'maxmin_300'  : [0, 1], 
        'maxmin_10' : [0, 1], 
        'maxmin_5'  : [0, 1],   
        'ha_colour_1': [0, 1],
        'ha_colour_2': [0, 1],
        'ewm_0.05': [-1, 1],
        'ewm_0.01': [-1, 1],
        'ewm_0.1': [-1, 1],
        'pct_sum_150': [-10, 10],
        'pct_sum_30' : [-10, 10],
        'pct_sum_10' : [-10, 10],
        'rsi_30': [0, 100],
        'rsi_10' : [0, 100],
        'rsi_20': [0, 100],
        'rsi_5' : [0, 100],
        'rsi_20_avg_3' : [-10, 10],
        'pct_diff_30_5' : [-10, 10],
        'rsi_14_avg_5' : [-10, 10],
        'pct_diff_150_5'  : [-10, 10],
        'pct_diff_150_30'  : [-10, 10],
        'pct_sum_3' : [-10, 10],
        'rsi_14_diff' : [-10, 10],
        'rsi_20_diff' : [-10, 10]
        }

# dict_= {
#         'maxmin_1000' : [0, 1],
#         'maxmin_500'  : [0, 1],  
#         'maxmin_300'  : [0, 1],  
#         'maxmin_5'  : [0, 1],   
#         'ewm_0.05': [0, 1],
#         'ewm_0.01': [0, 1],
#         'pct_sum_150': [-10, 10],
#         'pct_sum_30' : [-10, 10],
#         'rsi_20': [0, 100],
#         'rsi_5' : [0, 100],
#         'rsi_14_avg_5' : [-10, 10],
#         'rsi_20_avg_3' : [-10, 10]
#         }

      
# dict_= {
#   'pct_diff_30_5' : [-10, 10]
# }
  
# dict_= {
#         'pct_diff_30_5' : [-10, 10],
#         'rsi_14_avg_5' : [-10, 10],
#         'pct_diff_150_5'  : [-10, 10],
#         'pct_diff_150_30'  : [-10, 10],
#         'pct_sum_3' : [-10, 10],
#         'rsi_14_diff' : [-10, 10],
#         'rsi_20_diff' : [-10, 10]

# }

for i in range(1000):
  
  print(f'Cycle number is {i}:')
  print('='*50)

  opt_valid_fun_value = 0 
  opt_fun_value = 0

  g_k = 230
  n_parts = 1
  # p0, p1, max_fun_value = parameters_optimization(dict_, fun, pd.concat([data_train_whole, data_valid_whole]), data_valid_whole, n_parts, trade_type)
  p0, p1, max_fun_value = parameters_optimization(dict_, fun, data_train_whole, n_parts, trade_type)
  print(p0, p1, max_fun_value)

  #saving the model
  version = '141'
  model = class_models(p0, p1)
  model_name = f'model_v{str(version)}_fv{opt_fun_value:.0f}_vfv{opt_valid_fun_value:.0f}'
  folder_name = f'models_v{str(version)}'
  save_model(model, model_name, folder_name)

Cycle number is 0:
Stage number is 0
Cycle number is 0
train:: Functional value is 3970.000, mean is 3970.000, std is 1.000, profit is 3.600, prop is 21.000, total_wins is 21, total_loses is 1
valid:: Functional value is 2600.000, mean is 2600.000, std is 1.000, profit is 2.600, prop is 13.000, total_wins is 13, total_loses is 0
test:: Functional value is 200.000, mean is 200.000, std is 1.000, profit is 0.200, prop is 1.000, total_wins is 1, total_loses is 0
GLOBAL k is 600
p0 is [0.0, 0.0, 0.0, 0.4, 0.0, 0.0, 0.0, -0.40000000000000013, -0.15999999999999925, -1.0, -10.0, -1.5000000000000302, -10.0, 45.0, 55.0, 0.0, 0.0, -10.0, -10.0, -10.0, -2.0, -1.8999999999999808, -10.0, -10.0, -10.0]
p1 is [0.18999999999999928, 0.1000000000000002, 0.2999999999999994, 1.0, 1.0, 1.0, 1.0, 0.20000000000000018, 0.0999999999999992, 1.0, 1.0, 10.0, 10.0, 56.0, 100.0, 60.0, 100.0, 3.300000000000024, 10.0, 5.0, 10.0, 10.0, 10.0, 9.0, 10.0]
p0_opt_valid is [0.0, 0.0, 0.0, 0.4, 0.0, 0.0, 0.0, -0.40000000000

KeyboardInterrupt: 

In [223]:
opt_valid_fun_value = 0 
opt_fun_value = 0

version = '101'
model = class_models(p0, p1)
model_name = f'model_v{str(version)}_fv{opt_fun_value}_vfv{opt_valid_fun_value}'
folder_name = 'models_v101'
save_model(model, model_name, folder_name)

Model save completed


In [218]:
print(p0, p1, max_fun_value)

[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, -1.0, -0.40000000000000013, -1.0, -10.0, -10.0, -10.0, 0.0, 55.0, 50.0, 0.0, 1.0, -10.0, -10.0, -10.0, -3.0, -10.0, 2.0, -10.0] [0.30000000000000016, 0.1000000000000002, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 0.20000000000000018, 1.0, 10.0, 10.0, 10.0, 56.0, 100.0, 100.0, 100.0, 3.0, 10.0, 2.0, 10.0, 10.0, 0.0, 10.0, 9.0] 7400.0


In [200]:
# p0 = [0.0, 0.0, 0.1, 0.4, 0.0, 0.0, 0.0, -0.11999999999999922, -1.0, -1.0, -10.0, -10.0, -10.0, 0.0, 60.0, 50.0, 0.0, -10.0, -10.0, -10.0, -2.0, -2.0, -10.0, -10.0, -10.0]
# p1 = [0.18999999999999928, 0.1000000000000002, 0.30000000000000016, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 0.9999999999999787, 10.0, 0.9000000000000323, 50.0, 100.0, 100.0, 100.0, 4.0, 10.0, 5.0, 10.0, 10.0, 10.0, 9.0, 10.0]
# p0 = [0.0, 0.0, 0.1, 0.4, 0.0, 0.0, 0.0, -0.1000000000000002, -0.15999999999999925, -1.0, -10.0, -1.5000000000000302, -10.0, 45.0, 60.0, 50.0, 0.0, -10.0, -10.0, -10.0, -2.0, -1.8999999999999808, -10.0, -10.0, -10.0]
# p1 = [0.18999999999999928, 0.1000000000000002, 0.30000000000000016, 1.0, 1.0, 1.0, 1.0, 1.0, 0.0999999999999992, 1.0, 1.0, 10.0, 10.0, 50.0, 100.0, 60.0, 100.0, 4.0, 10.0, 5.0, 10.0, 10.0, 10.0, 9.0, 10.0]
# p0 = [0.0, 0.0, 0.1, 0.4, 0.0, 0.0, 0.0, -0.1000000000000002, -0.95, -1.0, -10.0, -10.0, 0.0, 0.0, 60.0, 50.0, 0.0, -10.0, -10.0, -10.0, -2.0, -2.0, -10.0, -10.0, -10.0]
# p1 = [0.18999999999999928, 0.1000000000000002, 0.30000000000000016, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 10.0, 10.0, 50.0, 100.0, 100.0, 100.0, 4.0, 10.0, 5.0, 10.0, 10.0, 10.0, 9.0, 10.0]
# p0 = [0.1, 0.0, 0.0, 0.0, 0.30000000000000004, 0.0, 0.0, -1.0, -1.0, -1.0, -10.0, -10.0, -10.0, 0.0, 55.0, 50.0, 0.0, 0.0, -10.0, -10.0, -2.0, -10.0, -10.0, -10.0, -1.0]
# p1 = [0.18999999999999928, 0.1000000000000002, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 0.0999999999999992, 1.0, 10.0, 10.0, 10.0, 100.0, 100.0, 100.0, 100.0, 10.0, 10.0, 10.0, 10.0, 0.0, 10.0, 10.0, 4.0]

# train 7.667 test 1.250
p0 =  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, -0.1000000000000002, -1.0, -1.0, -10.0, -10.0, -10.0, 45.0, 0.0, 0.0, 70.0, 2.0, -10.0, 2.0, -2.0, -1.9000000000000288, 0.0, -10.0, -10.0]
p1 = [0.18999999999999928, 0.1000000000000002, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 0.1000000000000002, 1.0, 10.0, 10.0, 10.0, 100.0, 65.0, 100.0, 80.0, 3.300000000000024, 10.0, 10.0, 10.0, 0.0, 10.0, 10.0, 10.0]
# train 5.294 test 1.455
p0 = [0.0, 0.0, 0.1, 0.8, 0.0, 0.0, 0.0, -1.0, -0.1000000000000002, -1.0, -10.0, -1.0, 0.0, 45.0, 55.0, 0.0, 0.0, -10.0, -10.0, -10.0, -10.0, -1.0, -10.0, -10.0, -10.0]
p1 = [0.18999999999999928, 0.1000000000000002, 0.30000000000000016, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 10.0, 10.0, 50.0, 100.0, 100.0, 80.0, 4.0, 10.0, 5.0, 10.0, 1.0, 10.0, 10.0, 4.0]

# train 4.714 test 5.000
p0 = [0.0, 0.0, 0.0, 1.0, 0.0, 0.1, 0.0, -0.40000000000000013, -0.15999999999999925, -1.0, -10.0, -1.5000000000000302, -10.0, 50.0, 55.0, 0.0, 0.0, -10.0, -10.0, 1.0, -1.0, -1.8999999999999808, -10.0, -3.0, -10.0]
p1 = [1.0, 0.1000000000000002, 0.2999999999999994, 1.0, 1.0, 1.0, 1.0, 0.20000000000000018, 0.0999999999999992, 1.0, 1.0, 10.0, 10.0, 56.0, 65.0, 60.0, 100.0, 3.300000000000024, 10.0, 3.0, 10.0, 10.0, 10.0, 5.0, 10.0]

# train 12.8 test 6.000
p0 = [0.0, 0.0, 0.1, 0.37, 0.1, 0.0, 0.0, -1.0, -0.13999999999999924, -1.0, -10.0, -10.0, -10.0, 0.0, 55.0, 0.0, 0.0, -10.0, 0.0, -1.0, -1.0, -10.0, -10.0, -10.0, -10.0]
p1 = [1.0, 0.0999999999999992, 1.0, 1.0, 1.0, 1.0, 1.0, 0.08999999999999919, 1.0, 1.0, 10.0, 10.0, 10.0, 50.0, 100.0, 100.0, 100.0, 3.0, 1.0, 10.0, 0.0, 10.0, 10.0, 10.0, 4.0]

# train 15 test 1.667
p0 = [0.0, 0.0, 0.0, 0.0, 0.18, 0.0, 0.0, -1.0, -0.1000000000000002, -1.0, -10.0, -10.0, -10.0, 45.0, 0.0, 0.0, 65.0, -10.0, -10.0, 3.0, -3.0, -10.0, -10.0, -10.0, -10.0]
p1 = [0.20000000000000018, 0.1000000000000002, 1.0, 0.9, 1.0, 1.0, 1.0, 1.0, 0.1000000000000002, 1.0, 10.0, 10.0, 10.0, 100.0, 100.0, 55.0, 85.0, 3.000000000000025, 10.0, 10.0, 10.0, 10.0, 10.0, 3.999999999999986, 10.0]

# train 7.714 test 2.500
p0 =  [0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, -1.0, -1.0, -1.0, -10.0, 0.0, -10.0, 44.0, 0.0, 0.0, 70.0, 1.0, -10.0, -10.0, -10.0, -1.0, -10.0, -10.0, -10.0]
p1 = [1.0, 0.1000000000000002, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 0.1000000000000002, 1.0, 10.0, 10.0, 10.0, 100.0, 100.0, 100.0, 85.0, 10.0, 10.0, 2.0, 10.0, 2.0, 10.0, 10.0, 10.0]

# train 7.2 test 1.667
p0 = [0.0, 0.0, 0.0, 0.99, 0.0, 0.0, 0.0, -1.0, -2.220446049250313e-16, -1.0, -0.9999999999999787, -10.0, 0.0, 45.0, 55.0, 0.0, 0.0, -10.0, -10.0, -10.0, -10.0, -10.0, -10.0, -10.0, 2.0]
p1 =[1.0, 0.1000000000000002, 0.20000000000000018, 1.0, 1.0, 1.0, 1.0, 0.08999999999999919, 0.0999999999999992, 1.0, 10.0, 10.0, 10.0, 100.0, 65.0, 55.0, 84.0, 3.300000000000024, 10.0, 10.0, 10.0, 10.0, 10.0, 10.0, 4.0]

# train 4.588 test 1.750
p0 = [0.0, 0.0, 0.0, 0.8, 0.0, 0.0, 0.0, -1.0, -0.15999999999999925, -1.0, -10.0, -10.0, -10.0, 45.0, 55.0, 0.0, 0.0, -9.0, -10.0, -10.0, -1.0, -1.8999999999999808, -10.0, -10.0, -10.0]
p1 = [0.18999999999999928, 0.1000000000000002, 0.2999999999999994, 1.0, 1.0, 1.0, 1.0, 1.0, 0.0999999999999992, 1.0, 10.0, 10.0, 10.0, 50.0, 100.0, 55.0, 100.0, 3.0, 10.0, 10.0, 10.0, 10.0, 0.0, 5.0, 10.0]

# train 9.250 test 3.000
p0 = [0.1, 0.0, 0.0, 0.4, 0.0, 0.1, 0.0, -1.0, -2.220446049250313e-16, -1.0, -10.0, -10.0, -10.0, 0.0, 55.0, 45.0, 59.0, -10.0, -10.0, -10.0, -2.0, -10.0, -10.0, -10.0, -10.0]
p1 = [0.18999999999999928, 0.1000000000000002, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 0.1000000000000002, 1.0, 10.0, 10.0, 10.0, 100.0, 65.0, 100.0, 100.0, 10.0, 10.0, 10.0, 10.0, 10.0, 10.0, 10.0, 4.0]

# train 7.571 test 1.000
p0 =  [0.0, 0.0, 0.0, 0.0, 0.9, 0.0, 0.0, -2.220446049250313e-16, -1.0, -1.0, -10.0, 0.0, -10.0, 45.0, 55.0, 0.0, 0.0, 1.0, -10.0, 0.9999999999999609, -2.0, -10.0, -10.0, -3.6000000000000227, -10.0]
p1 = [0.20000000000000018, 0.1000000000000002, 0.20000000000000018, 1.0, 1.0, 1.0, 1.0, 1.0, 0.1000000000000002, 1.0, 10.0, 10.0, 10.0, 100.0, 100.0, 56.0, 85.0, 3.300000000000024, 0.0, 5.0, 10.0, 10.0, 10.0, 10.0, 3.999999999999986]

# train 8.5 test 1.000
p0 = [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, -1.0, -0.40000000000000013, -1.0, -10.0, -10.0, -10.0, 0.0, 55.0, 50.0, 0.0, 1.0, -10.0, -10.0, -10.0, -3.0, -10.0, 2.0, -10.0]
p1 = [0.30000000000000016, 0.1000000000000002, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 0.20000000000000018, 1.0, 10.0, 10.0, 10.0, 56.0, 100.0, 100.0, 100.0, 3.0, 10.0, 2.0, 10.0, 10.0, 0.0, 10.0, 9.0]

for i, key in enumerate(dict_):
  dict_[key] = [p0[i], p1[i]]

fun(dict_, data_train_whole, 1, trade_type, 'train')
fun(dict_, data_test_whole , 1, trade_type, 'test')

train:: Functional value is 6600.000, mean is 6600.000, std is 1.000, profit is 6.600, prop is 8.500, total_wins is 51, total_loses is 6
test:: Functional value is -2000.000, mean is -2000.000, std is 1.000, profit is 0.000, prop is 1.000, total_wins is 5, total_loses is 5


(-2000.0, 250)

In [118]:
for i, key in enumerate(dict_.keys()):
  print(key)

maxmin_1000
maxmin_500
maxmin_300
maxmin_10
maxmin_5
ha_colour_1
ha_colour_2
ewm_0.05
ewm_0.01
ewm_0.1
pct_sum_150
pct_sum_30
pct_sum_10
rsi_30
rsi_10
rsi_20
rsi_5
rsi_20_avg_3
pct_diff_30_5
rsi_14_avg_5
pct_diff_150_5
pct_diff_150_30
pct_sum_3
rsi_14_diff
rsi_20_diff


In [201]:
models = []

p0 =  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, -0.1000000000000002, -1.0, -1.0, -10.0, -10.0, -10.0, 45.0, 0.0, 0.0, 70.0, 2.0, -10.0, 2.0, -2.0, -1.9000000000000288, 0.0, -10.0, -10.0]
p1 = [0.18999999999999928, 0.1000000000000002, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 0.1000000000000002, 1.0, 10.0, 10.0, 10.0, 100.0, 65.0, 100.0, 80.0, 3.300000000000024, 10.0, 10.0, 10.0, 0.0, 10.0, 10.0, 10.0]
model = class_models(p0, p1)
models.append(model)

p0 = [0.0, 0.0, 0.1, 0.8, 0.0, 0.0, 0.0, -1.0, -0.1000000000000002, -1.0, -10.0, -1.0, 0.0, 45.0, 55.0, 0.0, 0.0, -10.0, -10.0, -10.0, -10.0, -1.0, -10.0, -10.0, -10.0]
p1 = [0.18999999999999928, 0.1000000000000002, 0.30000000000000016, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 10.0, 10.0, 50.0, 100.0, 100.0, 80.0, 4.0, 10.0, 5.0, 10.0, 1.0, 10.0, 10.0, 4.0]
model = class_models(p0, p1)
models.append(model)

p0 = [0.0, 0.0, 0.0, 1.0, 0.0, 0.1, 0.0, -0.40000000000000013, -0.15999999999999925, -1.0, -10.0, -1.5000000000000302, -10.0, 50.0, 55.0, 0.0, 0.0, -10.0, -10.0, 1.0, -1.0, -1.8999999999999808, -10.0, -3.0, -10.0]
p1 = [1.0, 0.1000000000000002, 0.2999999999999994, 1.0, 1.0, 1.0, 1.0, 0.20000000000000018, 0.0999999999999992, 1.0, 1.0, 10.0, 10.0, 56.0, 65.0, 60.0, 100.0, 3.300000000000024, 10.0, 3.0, 10.0, 10.0, 10.0, 5.0, 10.0]
model = class_models(p0, p1)
models.append(model)

p0 = [0.0, 0.0, 0.1, 0.37, 0.1, 0.0, 0.0, -1.0, -0.13999999999999924, -1.0, -10.0, -10.0, -10.0, 0.0, 55.0, 0.0, 0.0, -10.0, 0.0, -1.0, -1.0, -10.0, -10.0, -10.0, -10.0]
p1 = [1.0, 0.0999999999999992, 1.0, 1.0, 1.0, 1.0, 1.0, 0.08999999999999919, 1.0, 1.0, 10.0, 10.0, 10.0, 50.0, 100.0, 100.0, 100.0, 3.0, 1.0, 10.0, 0.0, 10.0, 10.0, 10.0, 4.0]
model = class_models(p0, p1)
models.append(model)

p0 = [0.0, 0.0, 0.0, 0.0, 0.18, 0.0, 0.0, -1.0, -0.1000000000000002, -1.0, -10.0, -10.0, -10.0, 45.0, 0.0, 0.0, 65.0, -10.0, -10.0, 3.0, -3.0, -10.0, -10.0, -10.0, -10.0]
p1 = [0.20000000000000018, 0.1000000000000002, 1.0, 0.9, 1.0, 1.0, 1.0, 1.0, 0.1000000000000002, 1.0, 10.0, 10.0, 10.0, 100.0, 100.0, 55.0, 85.0, 3.000000000000025, 10.0, 10.0, 10.0, 10.0, 10.0, 3.999999999999986, 10.0]
model = class_models(p0, p1)
models.append(model)

p0 = [0.0, 0.0, 0.0, 0.99, 0.0, 0.0, 0.0, -1.0, -2.220446049250313e-16, -1.0, -0.9999999999999787, -10.0, 0.0, 45.0, 55.0, 0.0, 0.0, -10.0, -10.0, -10.0, -10.0, -10.0, -10.0, -10.0, 2.0]
p1 =[1.0, 0.1000000000000002, 0.20000000000000018, 1.0, 1.0, 1.0, 1.0, 0.08999999999999919, 0.0999999999999992, 1.0, 10.0, 10.0, 10.0, 100.0, 65.0, 55.0, 84.0, 3.300000000000024, 10.0, 10.0, 10.0, 10.0, 10.0, 10.0, 4.0]
model = class_models(p0, p1)
models.append(model)

# p0 = [0.0, 0.0, 0.0, 0.8, 0.0, 0.0, 0.0, -1.0, -0.15999999999999925, -1.0, -10.0, -10.0, -10.0, 45.0, 55.0, 0.0, 0.0, -9.0, -10.0, -10.0, -1.0, -1.8999999999999808, -10.0, -10.0, -10.0]
# p1 = [0.18999999999999928, 0.1000000000000002, 0.2999999999999994, 1.0, 1.0, 1.0, 1.0, 1.0, 0.0999999999999992, 1.0, 10.0, 10.0, 10.0, 50.0, 100.0, 55.0, 100.0, 3.0, 10.0, 10.0, 10.0, 10.0, 0.0, 5.0, 10.0]
# model = class_models(p0, p1)
# models.append(model)

p0 = [0.1, 0.0, 0.0, 0.4, 0.0, 0.1, 0.0, -1.0, -2.220446049250313e-16, -1.0, -10.0, -10.0, -10.0, 0.0, 55.0, 45.0, 59.0, -10.0, -10.0, -10.0, -2.0, -10.0, -10.0, -10.0, -10.0]
p1 = [0.18999999999999928, 0.1000000000000002, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 0.1000000000000002, 1.0, 10.0, 10.0, 10.0, 100.0, 65.0, 100.0, 100.0, 10.0, 10.0, 10.0, 10.0, 10.0, 10.0, 10.0, 4.0]
model = class_models(p0, p1)
models.append(model)


In [22]:
import re

class class_borders():
  def __init__(self, value):
    self.num_loses = 0 
    self.num_wins = 0
    self.prop = 0
    self.value = value

folder_path = 'models_v103'

parent_path = os.getcwd()
folder_path = os.path.join(parent_path, folder_path)
models = []

for i, name in enumerate(os.listdir(folder_path)):
    data_path = os.path.join(folder_path, name)
    file = open(data_path, 'rb')
    model = pickle.load(file)

    valid_value = int(re.findall(r'vfv*\d+|vfv.\d+', name)[0][3:])
    if valid_value >=0:
      models.append(model)
      file.close()

borders = []
for border in [1, 2, 3]:
  border.append(class_borders(border))

vote = np.empty(len(models))
for border in [1, 2, 3]:
  num_wins = 0
  num_loses = 0
  for i in range(len(data_test_whole)):
    for j, model in enumerate(models):
      vote[j] = True
      for key, value in model.dict_.items():
        if data_test_whole[key][i] < value[0] or data_test_whole[key][i] > value[1]:
          vote[j] = False
          break
    
    if sum(vote) >= border:
      if data_test_whole['win_long'][i] == 1:
        num_wins += 1
      else:
        num_loses += 1

  if num_loses == 0:
    prop = num_wins
  else:
    prop = num_wins / num_loses
  print(f'border is {border}: num_wins is {num_wins}, num_loses is {num_loses}, prop is {prop:.2f}')

border is 1: num_wins is 85, num_loses is 66, prop is 1.29
border is 2: num_wins is 28, num_loses is 15, prop is 1.87
border is 3: num_wins is 14, num_loses is 3, prop is 4.67


In [23]:
conditions = False
folder_save_models_name = f'models_v36_{trade_type}_numpartslist_cond{conditions}'
parent_path = os.getcwd()
# folder_path = os.path.join(parent_path, 'historical_data/onestock/5m_aug')
folder_path = os.path.join(parent_path, 'historical_data/onestock/5m_raw_aug')

data_train_whole = pd.DataFrame()
data_test_whole = pd.DataFrame()
data_whole = pd.DataFrame()


Group1_0 =['APH',   'TEL',  'BRK.B',  'BLK',  'MMC',  'HON',  'ECL',  'MSFT',  'AAPL',  'CTAS',  'JCI',  'ITW',  'ADP',  'ACN',  'EMR',  'MSI',  'DIS', 
             'ISRG',  'ROP',  'ETN',  'AXP',  'LIN',  'ADI',  'AVGO',  'INTU',  'MCO',  'TXN',  'PH',  'SBUX',  'CSCO',  'AJG',  'NXPI',  'HD',  'JPM',  'CDNS', 
             'ROK',  'QCOM',  'MCHP',  'SPG',  'CARR',  'COST',  'SYK',  'IQV',  'TT',  'GS',  'MSCI',  'TDG',  'GOOGL',  'V',  'ADSK']

Group0_75 = ['ADSK', 'AMAT', 'KLAC', 'ADBE', 'GOOG', 'BAC', 'COF', 'SPGI', 'SHW', 'ON', 'AMZN', 'ABT', 'SNPS', 'AON', 'LRCX', 'ICE', 'META', 'MS', 
             'NKE', 'IDXX', 'APD', 'NVDA', 'CSX', 'AIG', 'LOW', 'EL', 'MDT', 'PNC', 'GM', 'MMM', 'NOW', 'CRM', 'FTNT', 'TJX', 'DHR', 'MA', 'F', 
             'INTC', 'PLD', 'CAT', 'TGT', 'DHI', 'FCX', 'CB', 'PEP', 'MNST', 'C',  'NSC',  'GD',  'CMG']

num_items= len(os.listdir(folder_path))
for i in range(num_items):
    item = os.listdir(folder_path)[i]

    stock_name = item[str.find(item, 'df_') + 3 : str.find(item, '_20')]

    if stock_name in Group1_0:

        data_path = os.path.join(folder_path, item)
        data = load_data_one_stock(data_path, condtitions = conditions)
        data = data_augmentation(data)
        # data = data[['pct_1', 'ewm_0.1', 'win_long', 'win_short']]
        data_whole = pd.concat([data_whole, data])
        # data_train, data_test = train_test_split(data, train_size = 0.125, shuffle = False)
        data_train, data_test = train_test_split(data, train_size = 0.5, shuffle = False)
        # data_train, data_test = train_test_split(data, train_size = 0.66, shuffle = False)

        n = data.shape[0]    
        data_train_whole = pd.concat([data_train_whole, data_train])
        data_test_whole = pd.concat([data_test_whole, data_test])

# data_train_whole, data_valid_whole = train_test_split(data_train_whole, train_size = 0.7, shuffle = False)

data_train_whole_copy = data_train_whole
# data_valid_whole_copy = data_valid_whole
data_test_whole_copy = data_test_whole

In [38]:
import re

class class_borders():
  def __init__(self, value):
    self.num_loses = 0 
    self.num_wins = 0
    self.prop = 0
    self.value = value

folder_path = 'models_v131'
test_data = data_test_whole_copy
models_valid_value = - 11200
print(f'models_valid_value is {models_valid_value}')

parent_path = os.getcwd()
folder_path = os.path.join(parent_path, folder_path)
models = []

for i, name in enumerate(os.listdir(folder_path)):
    data_path = os.path.join(folder_path, name)
    file = open(data_path, 'rb')
    model = pickle.load(file)

    try:
      valid_value = int(re.findall(r'vfv*\d+|vfv.\d+', name)[0][3:])
      if valid_value >= models_valid_value:
        models.append(model)
    except:
        models.append(model)
    file.close()

borders = []
for border in [1, 2, 3, 4, 5, 6, 7,8,9,10]:
  borders.append(class_borders(border))

vote = np.empty(len(models))

for i in range(len(test_data)):
  for j, model in enumerate(models):
    vote[j] = True
    for key, value in model.dict_.items():
      if test_data[key][i] < value[0] or test_data[key][i] > value[1]:
        vote[j] = False
        break
  for border in borders:
    if sum(vote) >= border.value:
      if test_data['win_long'][i] == 1:
        border.num_wins += 1
      else:
        border.num_loses += 1
for border in borders:
  if border.num_loses == 0:
    border.prop = border.num_wins
  else:
    border.prop = border.num_wins / border.num_loses
  print(f'border is {border.value}: num_wins is {border.num_wins}, num_loses is {border.num_loses}, prop is {border.prop:.2f}')

models_valid_value is -11200
border is 1: num_wins is 3, num_loses is 0, prop is 3.00
border is 2: num_wins is 1, num_loses is 0, prop is 1.00
border is 3: num_wins is 1, num_loses is 0, prop is 1.00
border is 4: num_wins is 1, num_loses is 0, prop is 1.00
border is 5: num_wins is 1, num_loses is 0, prop is 1.00
border is 6: num_wins is 1, num_loses is 0, prop is 1.00
border is 7: num_wins is 1, num_loses is 0, prop is 1.00
border is 8: num_wins is 1, num_loses is 0, prop is 1.00
border is 9: num_wins is 1, num_loses is 0, prop is 1.00
border is 10: num_wins is 1, num_loses is 0, prop is 1.00


In [122]:
data_test_whole['ewm_0.1'][5]

0.10786294558884642

In [ ]:
data_test.to_csv('sdf2.csv')

In [ ]:
for column in data_train_whole.columns:
   print(data_train_whole.groupby(['win_long'])[column].quantile(0.3))

In [ ]:
print((data_train_whole.max() - data_valid_whole.max()).to_string()), 

In [ ]:
data_validation.to_csv('data_validation.csv')

In [ ]:
data.to_csv('data.csv')

In [ ]:
for param in model.parameters():
  print(param.data)

In [ ]:
file = 'df_AAPL_2021-06-06_2023-06-18_5m.pkl'
parent_path = os.getcwd()
folder_path = os.path.join(parent_path, 'historical_data\\onestock\\5m_row')

item = 'df_AAPL_2021-06-06_2023-06-18_5m.pkl'

data_path = os.path.join(folder_path, item)
file = open(data_path, 'rb')
df_ = pickle.load(file)
file.close()
df_.to_csv(f'{data_path}.csv')



In [ ]:
data_path[str.find(data_path, 'df_') + 3 : str.find(data_path, '_20')]

'ZTS'

In [ ]:
conditions = False
folder_save_models_name = f'models_v36_{trade_type}_numpartslist_cond{conditions}'
parent_path = os.getcwd()
# folder_path = os.path.join(parent_path, 'historical_data/onestock/5m_aug')
folder_path = os.path.join(parent_path, 'historical_data/onestock/1d_raw_test')

df = pd.DataFrame()


num_items= len(os.listdir(folder_path))
for i in range(num_items):
    item = os.listdir(folder_path)[i]

    data_path = os.path.join(folder_path, item)
    data = load_data_one_stock(data_path, condtitions = conditions)
    stock_name = data_path[str.find(data_path, 'df_') + 3 : str.find(data_path, '_20')]
    if df.shape[0] == 0:    
        df[stock_name] = data['pct']
    elif df.shape[0] == data.shape[0]:
        df[stock_name] = data['pct']

In [ ]:
df.corr().mean().sort_values(ascending=False)

APH      0.487274
TEL      0.461119
BRK.B    0.460872
BLK      0.454795
MMC      0.452170
           ...   
VLO      0.197716
MRNA     0.188305
BMY      0.177978
MRK      0.177865
ATVI     0.177287
Length: 197, dtype: float64

In [ ]:
df_corr  = df.corr().mean().sort_values(ascending=False)
df_corr.quantile(1)

0.48727444514244334

In [ ]:
corr_groups['Group0.75']

['ADSK',
 'AMAT',
 'KLAC',
 'ADBE',
 'GOOG',
 'BAC',
 'COF',
 'SPGI',
 'SHW',
 'ON',
 'AMZN',
 'ABT',
 'SNPS',
 'AON',
 'LRCX',
 'ICE',
 'META',
 'MS',
 'NKE',
 'IDXX',
 'APD',
 'NVDA',
 'CSX',
 'AIG',
 'LOW',
 'EL',
 'MDT',
 'PNC',
 'GM',
 'MMM',
 'NOW',
 'CRM',
 'FTNT',
 'TJX',
 'DHR',
 'MA',
 'F',
 'INTC',
 'PLD',
 'CAT',
 'TGT',
 'DHI',
 'FCX',
 'CB',
 'PEP',
 'MNST',
 'C',
 'NSC',
 'GD',
 'CMG']

In [ ]:
# corr_groups = {'Group0.25': [], 'Group0.5': [], 'Group0.75': [], 'Group1.0': [] }
step = 0.25
corr_groups = {}
for i in np.arange(0, 1.001 - step , step):
    corr_groups[f'Group{i + step}'] = []

df_corr  = df.corr().mean().sort_values(ascending=False)

for i in np.arange(0, 1.001 - step, step):
    for j in range(df_corr.shape[0]):
        if (df_corr.iloc[j] >= df_corr.quantile(i)) and  (df_corr.iloc[j] <= df_corr.quantile(i + step)):
            corr_groups[f'Group{i + step}'].append(df_corr.index[j])

corr_groups

{'Group0.25': ['SRE',
  'PANW',
  'WMB',
  'EXC',
  'CI',
  'TSLA',
  'ELV',
  'AZO',
  'WELL',
  'CME',
  'PG',
  'AEP',
  'T',
  'D',
  'VRTX',
  'BDX',
  'GILD',
  'CVX',
  'DUK',
  'MCK',
  'VZ',
  'HUM',
  'AMGN',
  'CL',
  'PM',
  'LMT',
  'COP',
  'WMT',
  'JNJ',
  'SO',
  'KMB',
  'XOM',
  'EOG',
  'REGN',
  'MPC',
  'ABBV',
  'PSX',
  'NOC',
  'PXD',
  'SLB',
  'LLY',
  'OXY',
  'GIS',
  'PFE',
  'MO',
  'VLO',
  'MRNA',
  'BMY',
  'MRK',
  'ATVI'],
 'Group0.5': ['CMG',
  'PYPL',
  'O',
  'HCA',
  'UPS',
  'MAR',
  'KO',
  'ORCL',
  'MDLZ',
  'MU',
  'HLT',
  'AMT',
  'EW',
  'GE',
  'ANET',
  'BSX',
  'RTX',
  'WM',
  'CMCSA',
  'BA',
  'FDX',
  'SCHW',
  'TMO',
  'PCAR',
  'EQIX',
  'AMD',
  'DXCM',
  'NFLX',
  'ZTS',
  'USB',
  'TFC',
  'CCI',
  'BKNG',
  'ORLY',
  'MCD',
  'PSA',
  'CVS',
  'IBM',
  'UNH',
  'WFC',
  'DE',
  'CHTR',
  'PGR',
  'STZ',
  'NUE',
  'UNP',
  'TMUS',
  'NEE',
  'ADM',
  'SRE'],
 'Group0.75': ['ADSK',
  'AMAT',
  'KLAC',
  'ADBE',
  'GOOG',
  'BA

In [ ]:
df2 = df[corr_groups['Group1.0']]
df2.corr().mean().sort_values(ascending=False)

APH      0.642299
TEL      0.611753
MSFT     0.586627
AAPL     0.579890
ACN      0.579602
BLK      0.577747
JCI      0.574687
ADI      0.572852
CTAS     0.572597
ECL      0.566280
MMC      0.561611
INTU     0.561049
AVGO     0.559388
NXPI     0.557255
TXN      0.556877
ITW      0.555959
ETN      0.553282
MCHP     0.552733
HON      0.552419
QCOM     0.549684
CDNS     0.549138
MSI      0.548787
ISRG     0.545121
DIS      0.543095
ADP      0.542988
EMR      0.542309
MCO      0.540672
ROP      0.540671
ROK      0.535164
ADSK     0.535098
MSCI     0.534599
GOOGL    0.533313
CARR     0.533021
BRK.B    0.532652
LIN      0.532515
SBUX     0.532017
AXP      0.531585
PH       0.528928
TT       0.524405
HD       0.519763
IQV      0.515862
CSCO     0.509578
COST     0.507976
TDG      0.506062
V        0.501959
AJG      0.500491
GS       0.497893
SPG      0.494261
SYK      0.494194
JPM      0.488870
dtype: float64